In [ ]:
#necessary installs
!pip install ultralytics albumentations

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 799.6/799.6 kB 5.5 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-m

In [ ]:
#necessary libs
import requests
import os
import re
import shutil
from sklearn.model_selection import train_test_split
import torch
from ultralytics import YOLO
import albumentations as A
from albumentations.pytorch import ToTensorV2
import cv2

In [ ]:
def get_direct_download_link(yandex_disk_public_link):
    base_url = 'https://cloud-api.yandex.net/v1/disk/public/resources/download?public_key='
    final_url = base_url + yandex_disk_public_link
    response = requests.get(final_url)
    download_url = response.json()['href']
    return download_url

yandex_disk_link = 'https://disk.yandex.ru/d/bqLuiqfCOYB8Tg'
download_url = get_direct_download_link(yandex_disk_link)

response = requests.get(download_url)
with open('dataset.zip', 'wb') as f:
    f.write(response.content)

!unzip dataset.zip -d ./dataset

Streaming output truncated to the last 5000 lines.
  inflating: ./dataset/Dataset (Copy)/train/labels/67313fc8ba1f97c2_jpg.rf.befec5d9cf9a3d38af24b46cbe5d2bba.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6b61ba6f4b63c410_jpg.rf.703750c565d8ba0279c7428f104b72ed.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6bcdcb9358d40bda_jpg.rf.a2125edd6b94fb4955fc9113ed86d082.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6d4fcb5ef7c7252b_jpg.rf.401c50d7c2d56935d4a8271362518030.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6dc019fdd1e01ce4_jpg.rf.f51d147421b3c6a406faac694b06956f.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6ea2da0d1114cda1_jpg.rf.704342819bb9ba361201e1fb8200ffbf.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6f617c67c3d6ec02_jpg.rf.5c3e0283982922f57a9d671530deae0d.txt  
  inflating: ./dataset/Dataset (Copy)/train/labels/6fd37c54dd44378d_jpg.rf.24313739019b4d686b3eeb6b74722f0e.txt  
  inflating: ./dataset/Dataset (Copy)

In [ ]:
# paths to dir
train_images_dir = '/content/dataset/Dataset (Copy)/train/images'
train_labels_dir = '/content/dataset/Dataset (Copy)/train/labels'

# existence checking
if not os.path.exists(train_images_dir):
    raise ValueError(f"Directory {train_images_dir} does not exist.")
if not os.path.exists(train_labels_dir):
    raise ValueError(f"Directory {train_labels_dir} does not exist.")

image_files = [f for f in os.listdir(train_images_dir) if f.endswith('.jpg')]
annotation_files = [f.replace('.jpg', '.txt') for f in image_files]

# existence checking
if len(image_files) == 0:
    raise ValueError(f"No image files found in {train_images_dir}.")
if len(annotation_files) == 0:
    raise ValueError(f"No annotation files found in {train_labels_dir}.")

# train and val split
train_images, val_images, train_annotations, val_annotations = train_test_split(
    image_files, annotation_files, test_size=0.2, random_state=42)

# dir for val
val_images_dir = '/content/dataset/Dataset (Copy)/val/images'
val_labels_dir = '/content/dataset/Dataset (Copy)/val/labels'
os.makedirs(val_images_dir, exist_ok=True)
os.makedirs(val_labels_dir, exist_ok=True)

# dir for train
os.makedirs(train_images_dir, exist_ok=True)
os.makedirs(train_labels_dir, exist_ok=True)

# moving to val
for img, ann in zip(val_images, val_annotations):
    shutil.move(os.path.join(train_images_dir, img), os.path.join(val_images_dir, img))
    shutil.move(os.path.join(train_labels_dir, ann), os.path.join(val_labels_dir, ann))

# moving to train
for img, ann in zip(train_images, train_annotations):
    shutil.move(os.path.join(train_images_dir, img), os.path.join(train_images_dir, img))
    shutil.move(os.path.join(train_labels_dir, ann), os.path.join(train_labels_dir, ann))

# Update data.yaml
data_yaml_content = """
train: /content/dataset/Dataset (Copy)/train/images
val: /content/dataset/Dataset (Copy)/val/images

nc: 56  # Количество классов в вашем датасете
names:
  0: Watermelon
  1: Apple
  2: Banana
  3: Cabbage
  4: Carrot
  5: Cucumber
  6: Lemon
  7: Potato
  8: Tomato
  9: Grape
  10: Grapefruit
  11: Mango
  12: Orange
  13: Peach
  14: Pear
  15: Pomegranate
  16: Pineapple
  17: Pumpkin
  18: Radish
  19: Coconut
  20: Litchi
  21: Bell-pepper
  22: Broccoli
  23: Cantaloupe
  24: Common-fig
  25: Strawberry
  26: Beet
  27: Egg
  28: Eggplant
  29: Garlic
  30: Onion
  31: Bread
  32: Cheese
  33: Fish
  34: Shrimp
  35: Crab
  36: Lobster
  37: Beef
  38: Beetroot
  39: Cauliflower
  40: Chicken
  41: Chilli-pepper
  42: Corn
  43: Ginger
  44: Kiwi
  45: Leek
  46: Lettuce
  47: Lime
  48: Pasta
  49: Peas
  50: Pork
  51: Rice
  52: Spinach
  53: Sweet-potato
  54: Turnip
  55: Squid
"""

with open('/content/dataset/Dataset (Copy)/data.yaml', 'w') as file:
    file.write(data_yaml_content)

print("Dataset split and data.yaml updated successfully.")


Dataset split and data.yaml updated successfully.


In [ ]:
#anntotations dirs
train_labels_dir = '/content/dataset/Dataset (Copy)/train/labels'
val_labels_dir = '/content/dataset/Dataset (Copy)/val/labels'

# fixing annotations
def check_and_fix_annotations(labels_dir):
    for label_file in os.listdir(labels_dir):
        if label_file.endswith('.txt'):
            file_path = os.path.join(labels_dir, label_file)
            with open(file_path, 'r') as f:
                lines = f.readlines()

            new_lines = []
            for line in lines:
                parts = line.strip().split()
                if len(parts) == 5:
                    try:
                        # transform to correct style
                        parts = [float(p) if i != 0 else int(re.sub('[^0-9]', '', p)) for i, p in enumerate(parts)]
                        new_lines.append(" ".join(map(str, parts)) + '\n')
                    except ValueError:
                        # except incorrect file
                        print(f"Skipping invalid annotation in {file_path}: {line.strip()}")
                else:
                    print(f"Incorrect format in {file_path}: {line.strip()}")

            # rewrite good file
            with open(file_path, 'w') as f:
                f.writelines(new_lines)

# checking
check_and_fix_annotations(train_labels_dir)
check_and_fix_annotations(val_labels_dir)

print("Annotation check and fix complete.")

# Delete dublicated
def remove_duplicate_annotations(labels_dir):
    for label_file in os.listdir(labels_dir):
        if label_file.endswith('.txt'):
            file_path = os.path.join(labels_dir, label_file)
            with open(file_path, 'r') as f:
                lines = f.readlines()

            #
            unique_lines = list(dict.fromkeys(lines))

            # rewrite files
            with open(file_path, 'w') as f:
                f.writelines(unique_lines)

remove_duplicate_annotations(train_labels_dir)
remove_duplicate_annotations(val_labels_dir)

print("Duplicate annotation removal complete.")


Streaming output truncated to the last 5000 lines.
Incorrect format in /content/dataset/Dataset (Copy)/val/labels/000000069286_jpg.rf.e17cfc497da40c26599f3d8c359a27f3.txt: 2 0.351109375 0.47111538461538466 0.348390625 0.4823966346153846 0.34828125 0.4898028846153846 0.35778125 0.49294350961538463 0.362171875 0.49272475961538464 0.366140625 0.49064663461538466 0.36696874999999995 0.48636538461538464 0.36696874999999995 0.4788341346153846 0.36478125 0.46892788461538465 0.35350000000000004 0.46714663461538464 0.351828125 0.4674591346153846 0.351109375 0.47111538461538466
Incorrect format in /content/dataset/Dataset (Copy)/val/labels/000000069286_jpg.rf.e17cfc497da40c26599f3d8c359a27f3.txt: 2 0.30146875 0.4836935096153846 0.303734375 0.48869350961538466 0.303734375 0.49194350961538463 0.305234375 0.4931935096153846 0.308484375 0.4946935096153846 0.310984375 0.4956935096153846 0.31248437500000004 0.4909435096153846 0.31448437500000004 0.4901935096153846 0.31473437499999996 0.484943509615384

In [ ]:
# Augmentation (it's will be enough)
def get_transform():
    return A.Compose([
        A.Rotate(limit=30, p=0.5),
        A.RandomBrightnessContrast(brightness_limit=0.2, contrast_limit=0, p=0.5),
        A.Normalize(mean=(0.485, 0.456, 0.406), std=(0.229, 0.224, 0.225)),
        ToTensorV2()
    ], bbox_params=A.BboxParams(format='yolo', label_fields=['class_labels']))

# Example of load and using augmentations
def load_and_augment_image(image_path, bboxes, transform):
    image = cv2.imread(image_path)
    transformed = transform(image=image, bboxes=bboxes, class_labels=[0] * len(bboxes))
    return transformed['image'], transformed['bboxes']

# fine-tuning and train
def train():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

    # Loading models
    model = YOLO("yolov8n.yaml").to(device)
    model = YOLO("yolov8n.pt").to(device)

    # Freezing weigths
    freeze = [f"model.{x}." for x in range(22)]
    for k, v in model.named_parameters():
        v.requires_grad = True
        if any(x in k for x in freeze):
            print(f"Freezing {k}")
            v.requires_grad = False

    # Path to dataset
    dataset_path = "/content/dataset/Dataset (Copy)/data.yaml"
    # Getting augmentations
    transform = get_transform()

    # Training
    model.train(data=dataset_path,
                imgsz=640,
                epochs=30,
                batch=16,
                name='yolov8_transfer_learning',
                device=device)

if __name__ == "__main__":
    train()

100%|██████████| 6.25M/6.25M [00:00<00:00, 234MB/s]


Freezing model.model.0.conv.weight
Freezing model.model.0.bn.weight
Freezing model.model.0.bn.bias
Freezing model.model.1.conv.weight
Freezing model.model.1.bn.weight
Freezing model.model.1.bn.bias
Freezing model.model.2.cv1.conv.weight
Freezing model.model.2.cv1.bn.weight
Freezing model.model.2.cv1.bn.bias
Freezing model.model.2.cv2.conv.weight
Freezing model.model.2.cv2.bn.weight
Freezing model.model.2.cv2.bn.bias
Freezing model.model.2.m.0.cv1.conv.weight
Freezing model.model.2.m.0.cv1.bn.weight
Freezing model.model.2.m.0.cv1.bn.bias
Freezing model.model.2.m.0.cv2.conv.weight
Freezing model.model.2.m.0.cv2.bn.weight
Freezing model.model.2.m.0.cv2.bn.bias
Freezing model.model.3.conv.weight
Freezing model.model.3.bn.weight
Freezing model.model.3.bn.bias
Freezing model.model.4.cv1.conv.weight
Freezing model.model.4.cv1.bn.weight
Freezing model.model.4.cv1.bn.bias
Freezing model.model.4.cv2.conv.weight
Freezing model.model.4.cv2.bn.weight
Freezing model.model.4.cv2.bn.bias
Freezing mode

/usr/local/lib/python3.10/dist-packages/torch/nn/modules/conv.py:456: UserWarning: Plan failed with a cudnnException: CUDNN_BACKEND_EXECUTION_PLAN_DESCRIPTOR: cudnnFinalize Descriptor Failed cudnn_status: CUDNN_STATUS_NOT_SUPPORTED (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:919.)
  return F.conv2d(input, weight, bias, self.stride,


AMP: checks passed ✅


train: Scanning /content/dataset/Dataset (Copy)/train/labels... 53440 images, 5741 backgrounds, 0 corrupt: 100%|██████████| 53440/53440 [01:35<00:00, 556.67it/s]


...

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()
val: Scanning /content/dataset/Dataset (Copy)/val/labels... 13361 images, 1429 backgrounds, 0 corrupt: 100%|██████████| 13361/13361 [00:28<00:00, 471.66it/s]


val: New cache created: /content/dataset/Dataset (Copy)/val/labels.cache
Plotting labels to runs/detect/yolov8_transfer_learning/labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: SGD(lr=0.01, momentum=0.9) with parameter groups 57 weight(decay=0.0), 64 weight(decay=0.0005), 63 bias(decay=0.0)
TensorBoard: model graph visualization added ✅
Image sizes 640 train, 640 val
Using 2 dataloader workers
Logging results to runs/detect/yolov8_transfer_learning
Starting training for 30 epochs...

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


       1/30      4.08G      1.257      3.896      1.516        100        640: 100%|██████████| 3340/3340 [23:58<00:00,  2.32it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 418/418 [03:13<00:00,  2.16it/s]


                   all      13361      38436      0.341      0.206      0.155     0.0966

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


       2/30      3.04G      1.291      3.012      1.517         50        640:  57%|█████▋    | 1914/3340 [13:33<07:17,  3.26it/s]